In [1]:
#P3 parser 含P4的next token
import re

outfile = open('P3_output.txt','w')
tmp_i = -1 #由於呼叫nexr_token都會將tmp_i+1所以initial為-1，此為輸入字串的index
token_list = [] #存抓到的token，包括他的parameter與值
tmp_token = ""  #暫存token
flag = 0   #0為正常，1為illegal，方便之後處理
Next=[]    #跟token_list是一樣的東西，用的地方不一樣

	# @(#)next_token(): 每次呼叫此function 就將傳入的input字串用regular expression做分析再依判斷式的結果
	#                   回傳部分字串
	#
	# FUNCTION:
	#           1.先判斷index是否正確 
	#           2.判斷是否已經抓到字串的最後一個，如果不是就繼續往下做
	#	    3.先判斷tmp_char是否為符號、字母或者數字，若遇到"/*"開頭的註解則跳過後面的字串
	#           4.每個判斷式裡面都有各自的return，return的是當下的token和token的type(存在token_list回傳)
	#	    
	# INPUT:
	#          使用者執行程式後自行輸入檔案名稱
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      每個判斷式裡面都有各自的return，return的是當下的token和token的type(存在token_list回傳)
		       
def next_token():
    global t
    global tmp_i
    global token_list
    global i
    token = ""
    token_list = []
    if tmp_i == len(t)-1:   #如果全部的token都抓完了就把token_list設為有空字串的list
        token_list = ["",""]
        return token_list
 
    tmp_i += 1
    tmp_char = t[tmp_i]
    if re.search("^[\+\-\>\=\<\(\)\*]$", tmp_char):
        #regular exp 從tmp_char裡尋找符合這些符號的pattern(^這個是起始符號 $結尾符號)
        if tmp_char == '>': #判斷目前的token是不是">"
            token += tmp_char #如果是">"就加到token裡
            if t[tmp_i+1] == '=':   #前面如果是">"就再判斷下一個是不是"="
                token += t[tmp_i+1] 
                tmp_i += 1
        elif tmp_char == '=': #判斷目前的token是不是"="
            token += tmp_char
            tmp_char = t[tmp_i+1]
            if tmp_char == '=': #前面如果是"="就再判斷下一個是不是"="
                token += tmp_char 
                tmp_i += 1
        else:
            token = tmp_char
        token_list.append(token)    #把抓到的token加到(append) token_list裡面作為return值
        return token_list
    elif re.search("^[a-z]$", tmp_char):
        #符合a~z(或是A~Z)的pattern
        token = tmp_char
        while True:
            if tmp_i == len(t)-1:   #如果index是最後一個就break
                break
            tmp_i += 1  	#index不是最後一個就把index加一
            if re.search("^[a-z0-9]$", t[tmp_i]):
                #index加一之後，就判斷有沒有符合a~z0~9的pattern(EX: a0,bB1,z9...)
                token += t[tmp_i]   #如有符合pattern就加到token
            else :
                #沒有符合a~z0~9的pattern，就讓index減一，然後break出while迴圈
                tmp_i -= 1
                break
        token_list.append("id")     #這裡是符合"id"這個pattern的，append到token_list
        token_list.append(token)    #把抓到的token加到(append) token_list裡面作為return值
        return token_list
    elif re.search("^[0-9]$", tmp_char) :
        #符合數字0~9的pattern
        token += tmp_char
        while True:
            if tmp_i == len(t)-1:   #如果index是最後一個就break
                break
            tmp_i += 1  	#index不是最後一個就把index加一
            tmp_char = t[tmp_i]
            if re.search("^[0-9]$", tmp_char):  #繼續判斷是不是數字0~9
                token += tmp_char
            else :
                #沒有符合0~9的pattern，就讓index減一，然後break出while迴圈
                tmp_i -= 1
                break
        token_list.append("num")    #這裡是符合"num"這個pattern的，append到token_list
        token_list.append(token)    #把抓到的token加到(append) token_list裡面作為return值
        return token_list
    elif tmp_char == '/':
        if t[tmp_i+1] == '*':
            #遇到/*開頭表示為註解 字串取到前面的部分就好
            t = t[0:tmp_i]
            tmp_i -= 1
            return " "

	# @(#)match(k): 每次呼叫此function 就將傳入的字串跟token比較是否相符合
	#                
	#
	# FUNCTION:
	#           1.先判斷傳入的字串跟token比較是否相符合
	#           2.再判斷flag這個變數是否為0(1為illegal時，0則legal)
	#	    3.再判斷當前match到的是哪種type(id,num,符號)，此為當前match進度
	#           4.呼叫next_token()抓下一個token
	#           5.return True代表文法正確，False則是文法錯誤
	#	    
	# INPUT:
	#          呼叫此function時傳入的參數值
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      return文法正確與否


def match(k):
    global lookahead
    global tmp_token
    global flag
    global Next
    global outfile
    if lookahead == k:      #判斷其他副程式在呼叫match()時，傳進來的字串是否與token一樣
        if flag == 0:   	#flag是在有illegal文法的時候會變成1其餘都是0 
            if lookahead == "num" or lookahead == "id": #如果token現在match到的是id或是num就把pattern跟它的值print出來
                print("此時match到", lookahead, Next[-1])
                print("此時match到", lookahead, Next[-1],file = outfile)
                
            else:
                print("此時match到",lookahead) #如果token現在match到的是符號就把它print出來
                print("此時match到",lookahead,file = outfile)
            Next = next_token() #用來存return回來的list
            lookahead = Next[0] #取list的index[0](代表是pattern)
            tmp_token += Next[-1]   #取list最後一項(num或id的值以及符號)  用來存有illegal文法時停下來的地方
        return True
    else:
        return False

	# @(#)factor(): 判斷factor根據grammar G1往下展開是符合哪種文法
	#                
	#
	# FUNCTION:
	#           1.判斷是否match到"("，再判斷expr()是否為True，再判斷是否match到")"，都成立return True
	#           2.判斷是否為num的type，return True
	#	    3.判斷是否為id的type，return True
	#           4.如果上述判斷式皆不成立，代表文法有誤，return False
	#           5.return True代表文法正確，False則是文法錯誤
	#           6.print出match進度
	#	    
	# INPUT:
	#          NONE!
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      return文法正確與否


def factor():
    global flag
    global outfile
    print("matching factor()")
    print("matching factor()",file = outfile)
    if match("("):  #如果match("(")左括號的值是True就往下判斷
        if expr():  #如果expr()是True就再往下判斷
            if match(")"):  #如果match(")")右括號的值是True代表factor -> (expr)這個文法是正確的，此次match有符合
                print("factor -> (expr)      OK")
                print("factor -> (expr)      OK",file = outfile)
                return True
            else:   #文法有錯flag改為1
                flag = 1
                return False
        flag = 1    #文法有錯flag改為1
        return False
    elif match("num"):  #如果match("num")的值是True代表factor -> num這個文法是正確的，此次match有符合
        print("factor -> num      OK")
        print("factor -> num      OK",file = outfile)
        return True
    
    elif match("id"):   #如果match("id")的值是True代表factor -> id這個文法是正確的，此次match有符合
        print("factor -> id      OK")
        print("factor -> id      OK",file = outfile)
        return True
    
    else:   #文法有錯flag改為1
        flag = 1
        return False


	# @(#)term_R(): 判斷term_R根據grammar G1往下展開是符合哪種文法
	#                
	#
	# FUNCTION:
	#           1.判斷是否match到"*"，如果沒有match到"*"，則文法符合term_R -> ε
	#           2.如果match到"*"，再判斷factor()是否為True，再判斷term_R()是否為True，都成立return True
	#           3.如果第2點判斷式其中之一不成立，代表文法有誤，return False
	#           4.print出match進度
	#	    
	# INPUT:
	#          NONE!
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      return文法正確與否

    
def term_R():
    global flag
    global outfile
    print("matching trem_R()")
    print("matching trem_R()",file = outfile)
    if match("*"):  #如果match("*")的值是True就往下判斷
        if factor():    #如果factor()的值是True就再往下判斷
            if term_R():    #如果term_R()的值是True代表term_R -> * factor term_R這個文法是正確的，此次match有符合
                print("term_R -> * factor term_R      OK")
                print("term_R -> * factor term_R      OK",file = outfile)
                return True
            else:   #文法有錯flag改為1
                flag = 1
                return False
        else:   #文法有錯flag改為1
            flag = 1
            return False
    else:   #代表此時的文法是term_R -> ε
        print("term_R -> ε      OK")
        print("term_R -> ε      OK",file = outfile)
        return 1

	# @(#)term(): 判斷term根據grammar G1往下展開是符合哪種文法
	#                
	#
	# FUNCTION:
	#           1.判斷factor()以及term_R()的回傳值，分別存在F、T_R兩個變數中，
	#           2.再判斷True或False
	#           3.print出match進度
	#	    
	# INPUT:
	#          NONE!
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      return文法正確與否
    
def term():
    global flag
    global outfile
    print("matching term()")
    print("matching term()",file = outfile)
    F = factor()    #儲存呼叫factor()後return的值
    T_R = term_R()  #儲存呼叫term_R()後return的值
    if (F == True) & (T_R == True): #都是True表示term -> factor term_R這個文法正確，此次match有符合
        print("term -> factor term_R      OK")
        print("term -> factor term_R      OK",file = outfile)
        return True
    else:   #文法有錯flag改為1
        flag = 1
        return False


	# @(#)add_R(): 判斷add_R根據grammar G1往下展開是符合哪種文法
	#                
	#
	# FUNCTION:
	#           1.判斷是否match到"+"，如果沒有match到"+"，則文法符合add_R -> ε
	#           2.如果match到"+"，再判斷term()是否為True，再判斷add_R()是否為True，都成立return True
	#           3.如果第2點判斷式其中之一不成立，代表文法有誤，return False
	#           4.print出match進度
	#	    
	# INPUT:
	#          NONE!
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      return文法正確與否


def add_R():
    global flag
    global outfile
    print("matching add_R")
    print("matching add_R",file = outfile)
    if match("+"):  #如果match("+")的值是True就往下判斷
        if term():  #如果term()的值是True就再往下判斷
            if add_R(): #如果add_R()的值是True代表add_R -> + term add_R這個文法是正確的，此次match有符合
                print("add_R -> + term add_R      OK")
                print("add_R -> + term add_R      OK",file = outfile)
                return True
            else:   #文法有錯flag改為1
                flag = 1
                return False
        else:   #文法有錯flag改為1
            flag = 1
            return False
    else:
        print("add_R -> ε      OK")
        print("add_R -> ε      OK",file = outfile)
        return 1


	# @(#)add(): 判斷add根據grammar G1往下展開是符合哪種文法
	#                
	#
	# FUNCTION:
	#           1.判斷term()以及add_R()的回傳值，分別存在T、A_R兩個變數中，
	#           2.再判斷True或False
	#           3.print出match進度
	#	    
	# INPUT:
	#          NONE!
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      return文法正確與否

    
def add():
    global flag
    global outfile
    print("matching add()")
    print("matching add()",file = outfile)
    T = term()      #儲存呼叫term()後return的值
    A_R = add_R()   #儲存呼叫add_R()後return的值
    if (T == True) & (A_R == True): #都是True表示add -> term add_R這個文法正確，此次match有符合
        print("add -> term add_R      OK")
        print("add -> term add_R      OK",file = outfile)
        return True
    else:   #文法有錯flag改為1
        flag = 1
        return False


	# @(#)rel_R(): 判斷rel_R根據grammar G1往下展開是符合哪種文法
	#                
	#
	# FUNCTION:
	#       1.判斷是否match到"<"，如果沒有match到"<"，再判斷是否match到"=="，如果沒有match到"=="，
	#
      #再判斷是否match到">="，如果都沒有match則文法屬於rel_R -> ε
	#       2.如果match到"<"，再判斷add()是否為True，再判斷rel_R()是否為True，都成立return True，
	#             如果第2點判斷式其中之一不成立，代表文法有誤，return False
	#       3.如果match到"=="，再判斷add()是否為True，再判斷rel_R()是否為True，都成立return True，
	#             如果第3點判斷式其中之一不成立，代表文法有誤，return False
	#       4.如果match到">="，再判斷add()是否為True，再判斷rel_R()是否為True，都成立return True，
	#             如果第4點判斷式其中之一不成立，代表文法有誤，return False
	#       5.print出match進度
	#	    
	# INPUT:
	#          NONE!
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      return文法正確與否


def rel_R():
    global flag
    global outfile
    print("matching rel_R()")
    print("matching rel_R()",file = outfile)
    if match("<"):  #如果match("<")的值是True就往下判斷
        if add():   #如果add()的值是True就再往下判斷
            if rel_R(): #如果rel_R()的值是True代表rel_R -> < add rel_R這個文法是正確的，此次match有符合
                print("rel_R -> < add rel_R      OK")
                print("rel_R -> < add rel_R      OK",file = outfile)
                return True
            else:   #文法有錯flag改為1
                flag = 1
                return False
        else:   #文法有錯flag改為1
            flag = 1
            return False
    elif match("=="):   #如果match("==")的值是True就往下判斷
        if add():   #如果add()的值是True就再往下判斷
            if rel_R(): #如果rel_R()的值是True代表rel_R -> == add rel_R這個文法是正確的，此次match有符合
                print("rel_R -> == add rel_R      OK")
                print("rel_R -> == add rel_R      OK",file = outfile)
                return True
            else:   #文法有錯flag改為1
                flag = 1
                return False
        else:   #文法有錯flag改為1
            flag = 1
            return False
    elif match(">="):   #如果match(">=")的值是True就往下判斷
        if add():   #如果add()的值是True就再往下判斷
            if rel_R(): #如果rel_R()的值是True代表rel_R -> >= add rel_R這個文法是正確的，此次match有符合
                print("rel_R -> >= add rel_R      OK")
                print("rel_R -> >= add rel_R      OK",file = outfile)
                return True
            else:   #文法有錯flag改為1
                flag = 1
                return False
        else:   #文法有錯flag改為1
            flag = 1
            return False
    else:
        print("rel_R -> ε      OK")
        print("rel_R -> ε      OK",file = outfile)
        return 1


	# @(#)rel(): 判斷rel根據grammar G1往下展開是符合哪種文法
	#                
	#
	# FUNCTION:
	#           1.判斷add()以及rel_R()的回傳值，分別存在A、R_R兩個變數中，
	#           2.再判斷True或False
	#           3.print出match進度
	#	    
	# INPUT:
	#          NONE!
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      return文法正確與否

        
def rel():
    global flag
    global outfile
    print("matching rel()")
    print("matching rel()",file = outfile)
    A = add()   #儲存呼叫add()後return的值
    R_R = rel_R()   #儲存呼叫rel_R()後return的值
    if (A == True) & (R_R == True): #都是True表示rel -> add rel_R這個文法正確，此次match有符合
        print("rel -> add rel_R      OK")
        print("rel -> add rel_R      OK",file = outfile)
        return True
    else:   #文法有錯flag改為1
        flag = 1
        return False


	# @(#)expr(): 判斷expr根據grammar G1往下展開是符合哪種文法
	#                
	#
	# FUNCTION:
	#           1.判斷rel()的回傳值是否為True
	#           2.再判斷是否match"="，如果沒有match"="，表示文法符合expr -> rel
	#           3.如果有match"="，再判斷expr()回傳值是否為True，都成立return True
	#           4.如果第3點判斷式其中之一不成立，代表文法有誤，return False
	#           5.print出match進度
	#	    
	# INPUT:
	#          NONE!
	# OUTPUT: 
	#	    NONE!
	#	    
	# RETURN:
	#      return文法正確與否

    
def expr():
    global flag
    global tmp_token
    global outfile
    print("matching expr()")
    print("matching expr()",file = outfile)
    if rel():   #如果rel()的值是True就往下判斷
        if match("="):  #如果match("=")的值是True就再往下判斷
            if expr():  #如果expr()的值是True代表expr -> rel = expr這個文法是正確的，此次match有符合
                print("expr -> rel = expr      OK")
                print("expr -> rel = expr      OK",file = outfile)
                return True
            else:   #文法有錯flag改為1
                flag = 1
                return False
        else:   #如果rel()為True後沒有"="，代表expr -> rel這個文法是正確的，此次的match有符合
            print("expr -> rel      OK")
            print("expr -> rel      OK",file = outfile)
            return True
    else:   #文法有錯flag改為1
        flag = 1
        return False


	# @(#)main(): 讓使用者輸入需要傳入的input file，並讀取檔案內容，再加以處理，以及輸出最終結果
	#                
	#
	# FUNCTION:
	#           1.讓使用者自行輸入檔案名稱
	#           2.利用迴圈讀取檔案內容(一次讀取一行)
	#           3.將參數初始化，並處理字串(將字串裡的空白去除)
	#           4.呼叫next_token()以及expr()往下展開
	#           5.顯示最終結果(成功或失敗)
	#	    
	# INPUT:
	#          使用者輸入的檔案名稱
	# OUTPUT: 
	#	    最終結果(文法正確與否)
	#	    
	# RETURN:
	#      NONE!


def main():
    global tmp_i
    global t
    global lookahead
    global tmp_token
    global Next
    global flag
    global outfile
    filename = input("Please enter your input file name:")
    linenum = 0
    for line in open(filename):
        linenum += 1
    f = open(filename,"r")
    for i in range(linenum):

        tmp_i = -1

        tmp_token = ""
        flag = 0
        Next=[]
        
        text = f.readline()
        t = text[0:-1].replace(' ','')
        Next = next_token()
        lookahead = Next[0]
        tmp_token = Next[-1]
        
        print("此時的字串:", t)
        print("此時的字串:", t,file = outfile)
        E = expr()
        t = ""
        text = ""
        if E == True:   #全部的文法都正確
            print("Success!!!")
            print("Success!!!",file = outfile)
        elif E == False:    #文法有錯，並把停下的地方顯示出來
            print("Failed")
            print("Failed",file = outfile)
            print("Parsing stops at : ", tmp_token)
            print("Parsing stops at : ", tmp_token,file = outfile)
        print()
        print(file = outfile)
    outfile.close()
    f.close()




main()


KeyboardInterrupt: ignored